Using SQL to update weather data

In [1]:
# sqlite3 library to run operations on the database
import sqlite3

gen_path = '/home/imants/gits/COVID-19/'

db_path = gen_path + 'sql/weather.db'

# connecting to the weather database
con = sqlite3.connect(db_path)

# establishing database cursor
cursorObj = con.cursor()


In [2]:
# Getting table names

table_names = cursorObj.execute("SELECT name FROM sqlite_master WHERE type='table';")

table_names = table_names.fetchall()

# Taking the table names that were fetched, and making a usable lists out of the values.

US_names = []
global_names = []

for x in range(len(table_names)):
    if (table_names[x][0][-2:] == 'US'):
        US_names.append(table_names[x][0])
        
    else:
        global_names.append(table_names[x][0])
        
 
print('US names', US_names)

print('Global names', global_names)
    


US names ['cloud_US', 'dew_US', 'humidity_US', 'ozone_US', 'precip_US', 'pressure_US', 'sunrise_US', 'sunset_US', 'tMax_US', 'tMin_US', 'uv_US', 'wind_US']
Global names ['cloud_Global', 'dew_Global', 'humidity_Global', 'ozone_Global', 'precip_Global', 'pressure_Global', 'sunrise_Global', 'sunset_Global', 'tMax_Global', 'tMin_Global', 'uv_Global', 'wind_Global']


In [ ]:
# getting table info

# query = 'SELECT * FROM {}'.format(US_names[0])
# cursorObj.execute(query)

# the_table = cursorObj.fetchall()

# the_table

In [ ]:
# adding dates to tables
# current last date is 8/12/20

for x in range(14, 32):
    
    day_str = str(x)
    date_str = '"8/' + day_str + '/20"'
    
    for y in US_names:
        
        add_str = 'ALTER TABLE {} ADD COLUMN {} text'.format(y, date_str)
        cursorObj.execute(add_str)
        print(add_str)
    
    for y in global_names:
        
        add_str = 'ALTER TABLE {} ADD COLUMN {} text'.format(y, date_str)
        cursorObj.execute(add_str)
        print(add_str)

In [3]:
# Reading API key

key_path = '/home/imants/gits/COVID-19/key.txt'

api_file = open(key_path, 'r')
API_KEY = api_file.read()
api_file.close()
API_KEY = API_KEY.strip()

API_KEY

'4c660453101c9bb8a7f8360c95eaf4c1'

In [4]:
# Creating API call function

import pandas as pd
import numpy as np
import requests
import json
from datetime import datetime as dt

def call_api (lat, long, time):
    
    # Building the URL for the API get
    url = 'https://api.darksky.net/forecast/' + API_KEY + '/' + lat + "," + long + ',' + time
    url = url + '?exclude=currently,flags&units=si'

    # Getting the API call
    # using the retry error handling established above
    # response = http.get(url)
    
    # Putting the API response into the JSON thing
    # info = json.loads(response.content)
    info = url
    
    return info

In [7]:
# update US locations

import pandas as pd
import numpy as np
import requests
import json
from datetime import datetime as dt

# Code to increase number of retries on connection errors,
# and also to give it some time.
# Found on https://stackoverflow.com/questions/15431044/can-i-set-max-retries-for-requests-request
# And https://findwork.dev/blog/advanced-usage-python-requests-timeouts-retries-hooks/

from urllib3.util.retry import Retry
from requests.adapters import HTTPAdapter

s = requests.Session()

retries = Retry(total=30,
                backoff_factor=0.1,
                status_forcelist=[ 429, 500, 502, 503, 504 ],
                method_whitelist=["HEAD", "GET", "OPTIONS"])

adapter = HTTPAdapter(max_retries=retries)
http = requests.Session()
http.mount("https://", adapter)
http.mount("http://", adapter)

# Dummy value in case of errors
dummy = '-1000'

# Making list of columns that need to be updated from prior update, above
columns_to_update = []

# Counting API calls
counter = 0

for x in range(13, 32):
    
    day_str = str(x)
    date_str = '"8/' + day_str + '/20"'
    columns_to_update.append(date_str)

for col_name in columns_to_update:
    
    tables = []
        
    for tab_name in US_names:
        
        query_string = 'SELECT Lat, "Long_", {} FROM {}'.format(col_name, tab_name)
        # print(query_string)
        cursorObj.execute(query_string)
        tables.append(cursorObj.fetchall())
        
        # names_test = cursorObj.execute(query_string).description
        # print(names_test[2][0], col_name)
        
    # print(len(tables[0]))
   
    # Create Unix time stamp out of the date column
    # stripping quotation marks from column name
    i = len(col_name)
    col_date = col_name[1:(i-1)]
    
    t = pd.to_datetime(col_date)
    t = int(t.value / 10**9)
    t = str(t)
    
    
    for y in range(len(tables[0])):
        
        latitude = str(tables[0][y][0])
        longitude = str(tables[0][y][1])
        
        # Calling API with latitude, longitude, and unix time
        info = call_api(latitude, longitude, t)
        
        counter = counter + 1
        
        print(info)
        print('Latitude: ', latitude, ', Longitude: ', longitude, ', Date: ', col_name)
        print('Unix time: ', t)
        
        
        # US names: [0: 'cloud_US', 1: 'dew_US', 2: 'humidity_US', 3: 'ozone_US', 4: 'precip_US', 5: 'pressure_US', 
        #           6: 'sunrise_US', 7: 'sunset_US', 8: 'tMax_US', 9: 'tMin_US', 10: uv_US', 11: 'wind_US']
       
        
        # getting values from the JSON response
        # adding error handling in case something is wrong with the JSON response
        try:

            # Making a variable to more easily acccess JSON response data
            easy_info = info['daily']['data'][0]

            # Reading the JSON data
            tMax = str(easy_info['temperatureHigh'])
            tMin = str(easy_info['temperatureLow'])
            hum = str(easy_info['humidity'] * 100)
            uvee = str(easy_info['uvIndex'])
            clouds = str(easy_info['cloudCover'] * 100)
            precip = str(easy_info['precipProbability'] * 100)
            dew = str(easy_info['dewPoint'])
            pressure = str(easy_info['pressure'])
            wind = str(easy_info['windSpeed'])
            ozone = str(easy_info['ozone'])
            sunrise = str(easy_info['sunriseTime'])
            sunset = str(easy_info['sunsetTime'])

        except:

            # Creating dummy values in case of error
            print('Error encountered')
            tMax = dummy
            tMin = dummy
            hum = dummy
            uvee = dummy
            clouds = dummy
            precip = dummy
            dew = dummy
            pressure = dummy
            wind = dummy
            ozone = dummy
            sunrise = dummy
            sunset = dummy

        
        where_str = 'Lat = {} AND Long_ = {}'.format(latitude, longitude)
        
        update_str = 'UPDATE {} SET {} = {} WHERE {}'.format('cloud_US', col_name, clouds, where_str)
        cursorObj.execute(update_str)
        
        update_str = 'UPDATE {} SET {} = {} WHERE {}'.format('dew_US', col_name, clouds, where_str)
        cursorObj.execute(update_str)
        
        update_str = 'UPDATE {} SET {} = {} WHERE {}'.format('humidity_US', col_name, clouds, where_str)
        cursorObj.execute(update_str)
        
        update_str = 'UPDATE {} SET {} = {} WHERE {}'.format('ozone_US', col_name, clouds, where_str)
        cursorObj.execute(update_str)
        
        update_str = 'UPDATE {} SET {} = {} WHERE {}'.format('precip_US', col_name, clouds, where_str)
        cursorObj.execute(update_str)
        
        update_str = 'UPDATE {} SET {} = {} WHERE {}'.format('pressure_US', col_name, clouds, where_str)
        cursorObj.execute(update_str)
        
        update_str = 'UPDATE {} SET {} = {} WHERE {}'.format('sunrise_US', col_name, clouds, where_str)
        cursorObj.execute(update_str)
        
        update_str = 'UPDATE {} SET {} = {} WHERE {}'.format('sunset_US', col_name, clouds, where_str)
        cursorObj.execute(update_str)
        
        update_str = 'UPDATE {} SET {} = {} WHERE {}'.format('tMax_US', col_name, clouds, where_str)
        cursorObj.execute(update_str)
        
        update_str = 'UPDATE {} SET {} = {} WHERE {}'.format('tMin_US', col_name, clouds, where_str)
        cursorObj.execute(update_str)
        
        update_str = 'UPDATE {} SET {} = {} WHERE {}'.format('uv_US', col_name, clouds, where_str)
        cursorObj.execute(update_str)
        
        update_str = 'UPDATE {} SET {} = {} WHERE {}'.format('wind_US', col_name, clouds, where_str)
        cursorObj.execute(update_str)
        
        
        
        
        # print(iteration[y][2])
# test_string = 'SELECT Lat, "Long_", "8/13/20" FROM cloud_US'

# cursorObj.execute(test_string)

# the_table = cursorObj.fetchall()

#the_table[0]
#print(tables[0][0])
#names_test = tables[0].description

#print(names_test)

https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/32.53952745,-86.64408227,1597276800?exclude=currently,flags&units=si
Latitude:  32.53952745 , Longitude:  -86.64408227 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 32.53952745 AND Long_ = -86.64408227
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/30.72774991,-87.72207058,1597276800?exclude=currently,flags&units=si
Latitude:  30.72774991 , Longitude:  -87.72207058 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 30.72774991 AND Long_ = -87.72207058
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/31.868263,-85.3871286,1597276800?exclude=currently,flags&units=si
Latitude:  31.868263 , Longitude:  -85.3871286 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 31.868263 AND Long_ = -85.3871286
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/32.99642064,-

Latitude:  35.39465006 , Longitude:  -109.4892383 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 35.39465006 AND Long_ = -109.4892383
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/31.87934684,-109.7516088,1597276800?exclude=currently,flags&units=si
Latitude:  31.87934684 , Longitude:  -109.7516088 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 31.87934684 AND Long_ = -109.7516088
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/35.83883429,-111.7707178,1597276800?exclude=currently,flags&units=si
Latitude:  35.83883429 , Longitude:  -111.7707178 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 35.83883429 AND Long_ = -111.7707178
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/33.80190085,-110.8132779,1597276800?exclude=currently,flags&units=si
Latitude:  33.80190085 , Longitude:  -110.8132779 , Date:  "8/13/20"
U

Latitude:  36.07409056 , Longitude:  -119.8159973 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 36.07409056 AND Long_ = -119.8159973
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/39.10124298,-122.7536244,1597276800?exclude=currently,flags&units=si
Latitude:  39.10124298 , Longitude:  -122.7536244 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 39.10124298 AND Long_ = -122.7536244
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/40.67311306,-120.59350990000002,1597276800?exclude=currently,flags&units=si
Latitude:  40.67311306 , Longitude:  -120.59350990000002 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 40.67311306 AND Long_ = -120.59350990000002
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/34.30828379,-118.2282411,1597276800?exclude=currently,flags&units=si
Latitude:  34.30828379 , Longitude:  -118.2282411

Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 39.97015535 AND Long_ = -103.202587
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/40.55499405,-104.3929621,1597276800?exclude=currently,flags&units=si
Latitude:  40.55499405 , Longitude:  -104.3929621 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 40.55499405 AND Long_ = -104.3929621
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/40.00346839,-102.4258673,1597276800?exclude=currently,flags&units=si
Latitude:  40.00346839 , Longitude:  -102.4258673 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 40.00346839 AND Long_ = -102.4258673
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/41.26809896,-73.3881171,1597276800?exclude=currently,flags&units=si
Latitude:  41.26809896 , Longitude:  -73.3881171 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 41.2

Latitude:  31.29633502 , Longitude:  -82.87545866 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 31.29633502 AND Long_ = -82.87545866
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/31.55456473,-82.45936528,1597276800?exclude=currently,flags&units=si
Latitude:  31.55456473 , Longitude:  -82.45936528 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 31.55456473 AND Long_ = -82.45936528
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/31.32669878,-84.44218806,1597276800?exclude=currently,flags&units=si
Latitude:  31.32669878 , Longitude:  -84.44218806 , Date:  "8/13/20"
Unix time:  1597276800
UPDATE cloud_US SET "8/13/20" = 1 WHERE Lat = 31.32669878 AND Long_ = -84.44218806
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/33.06882326,-83.24701748,1597276800?exclude=currently,flags&units=si
Latitude:  33.06882326 , Longitude:  -83.24701748 , Date:  "8/13/20"
U

...

Latitude:  38.35657051 , Longitude:  -113.2342232 , Date:  "8/18/20"
Unix time:  1597708800
UPDATE cloud_US SET "8/18/20" = 1 WHERE Lat = 38.35657051 AND Long_ = -113.2342232
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/41.52106798,-113.0832816,1597708800?exclude=currently,flags&units=si
Latitude:  41.52106798 , Longitude:  -113.0832816 , Date:  "8/18/20"
Unix time:  1597708800
UPDATE cloud_US SET "8/18/20" = 1 WHERE Lat = 41.52106798 AND Long_ = -113.0832816
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/41.72330587,-111.7443667,1597708800?exclude=currently,flags&units=si
Latitude:  41.72330587 , Longitude:  -111.7443667 , Date:  "8/18/20"
Unix time:  1597708800
UPDATE cloud_US SET "8/18/20" = 1 WHERE Lat = 41.72330587 AND Long_ = -111.7443667
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/39.64834818,-110.5872512,1597708800?exclude=currently,flags&units=si
Latitude:  39.64834818 , Longitude:  -110.5872512 , Date:  "8/18/20"
U

https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/38.88485255,-77.17560759,1597708800?exclude=currently,flags&units=si
Latitude:  38.88485255 , Longitude:  -77.17560759 , Date:  "8/18/20"
Unix time:  1597708800
UPDATE cloud_US SET "8/18/20" = 1 WHERE Lat = 38.88485255 AND Long_ = -77.17560759
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/38.73564842,-77.80647472,1597708800?exclude=currently,flags&units=si
Latitude:  38.73564842 , Longitude:  -77.80647472 , Date:  "8/18/20"
Unix time:  1597708800
UPDATE cloud_US SET "8/18/20" = 1 WHERE Lat = 38.73564842 AND Long_ = -77.80647472
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/36.9302126,-80.36738849,1597708800?exclude=currently,flags&units=si
Latitude:  36.9302126 , Longitude:  -80.36738849 , Date:  "8/18/20"
Unix time:  1597708800
UPDATE cloud_US SET "8/18/20" = 1 WHERE Lat = 36.9302126 AND Long_ = -80.36738849
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/37.8415

Unix time:  1597708800
UPDATE cloud_US SET "8/18/20" = 1 WHERE Lat = 37.12191123 AND Long_ = -81.56685568
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/36.73285734,-76.04566934,1597708800?exclude=currently,flags&units=si
Latitude:  36.73285734 , Longitude:  -76.04566934 , Date:  "8/18/20"
Unix time:  1597708800
UPDATE cloud_US SET "8/18/20" = 1 WHERE Lat = 36.73285734 AND Long_ = -76.04566934
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/38.90847745,-78.20280433,1597708800?exclude=currently,flags&units=si
Latitude:  38.90847745 , Longitude:  -78.20280433 , Date:  "8/18/20"
Unix time:  1597708800
UPDATE cloud_US SET "8/18/20" = 1 WHERE Lat = 38.90847745 AND Long_ = -78.20280433
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/36.72341572,-81.95666289,1597708800?exclude=currently,flags&units=si
Latitude:  36.72341572 , Longitude:  -81.95666289 , Date:  "8/18/20"
Unix time:  1597708800
UPDATE cloud_US SET "8/18/20" = 1 WHERE Lat = 3

Latitude:  37.612327 , Longitude:  -81.54511071 , Date:  "8/18/20"
Unix time:  1597708800
UPDATE cloud_US SET "8/18/20" = 1 WHERE Lat = 37.612327 AND Long_ = -81.54511071
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/43.96974651,-89.76782777,1597708800?exclude=currently,flags&units=si
Latitude:  43.96974651 , Longitude:  -89.76782777 , Date:  "8/18/20"
Unix time:  1597708800
UPDATE cloud_US SET "8/18/20" = 1 WHERE Lat = 43.96974651 AND Long_ = -89.76782777
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/46.31956891,-90.67837132,1597708800?exclude=currently,flags&units=si
Latitude:  46.31956891 , Longitude:  -90.67837132 , Date:  "8/18/20"
Unix time:  1597708800
UPDATE cloud_US SET "8/18/20" = 1 WHERE Lat = 46.31956891 AND Long_ = -90.67837132
https://api.darksky.net/forecast/4c660453101c9bb8a7f8360c95eaf4c1/45.42372701,-91.84833627,1597708800?exclude=currently,flags&units=si
Latitude:  45.42372701 , Longitude:  -91.84833627 , Date:  "8/18/20"
Unix 

KeyboardInterrupt: 

In [ ]:
# temporary home for this code
# adding error handling in case something is wrong with the JSON response
        try:

            # Making a variable to more easily acccess JSON response data
            easy_info = info['daily']['data'][0]

            # Reading the JSON data
            tMax = easy_info['temperatureHigh']
            tMin = easy_info['temperatureLow']
            hum = easy_info['humidity'] * 100
            uvee = easy_info['uvIndex']
            clouds = easy_info['cloudCover'] * 100
            precip = easy_info['precipProbability'] * 100
            dew = easy_info['dewPoint']
            pressure = easy_info['pressure']
            wind = easy_info['windSpeed']
            ozone = easy_info['ozone']
            sunrise = easy_info['sunriseTime']
            sunset = easy_info['sunsetTime']

        except:

            # Creating dummy values in case of error
            print('Error encountered')
            tMax = dummy
            tMin = dummy
            hum = dummy
            uvee = dummy
            clouds = dummy
            precip = dummy
            dew = dummy
            pressure = dummy
            wind = dummy
            ozone = dummy
            sunrise = dummy
            sunset = dummy


In [ ]:
for x in range(len(the_table)):
    print(x)

In [ ]:
# close database connection

con.close()